GS25 데이터 크롤링 

In [1]:
#post방식 = 주소에 데이터를 담아서 보내지 않음 = 선택할 때마다 주소값이 바뀌지 않는 것을 확인 = Payload 정보 필요
#아래 방식으로 진행하면 데이터를 받아오지 않음 
import requests
#CSRFToken Cross-Site Request Forqery 사이트 간 요청 위조 방지하기 위한 토큰 
url = "https://gs25.gsretail.com/gscvs/ko/store-services/locationList?CSRFToken=3a6c09a4-f4cf-4211-b4ad-b03594f24868"

payload = {"pageNum": "1",
"pageSize": "50000",
"searchShopName": "",
"searchSido": "11",
"searchGugun": "1168",
"searchDong": "11680118",
"searchType": "",
"searchTypeService": "0",
"searchTypeToto": "0",
"searchTypeCafe25": "0",
"searchTypeInstant": "0",
"searchTypeDrug": "0",
"searchTypeSelf25": "0",
"searchTypePost": "0",
"searchTypeATM": "0",
"searchTypeWithdrawal": "0",
"searchTypeTaxrefund": "0",
"searchTypeSmartAtm": "0",
"searchTypeSelfCookingUtensils": "0",
"searchTypeDeliveryService": "0",
"searchTypeParcelService": "0",
"searchTypePotatoes": "0",
"searchTypeCardiacDefi": "0",
"searchTypeFishShapedBun": "0",
"searchTypeWine25": "0",
"searchTypeGoPizza": "0",
"searchTypeSpiritWine": "0",
"searchTypeFreshGanghw": "0"}


r = requests.post(url, data=payload)
r.text 

'<!DOCTYPE html PUBLIC "-//W3C//DTD XHTML 1.0 Transitional//EN" "http://www.w3.org/TR/xhtml1/DTD/xhtml1-transitional.dtd">\r\n<html xmlns="http://www.w3.org/1999/xhtml" lang="ko" xml:lang="ko">\r\n<head>\r\n\t<meta http-equiv="X-UA-Compatible" content="IE=edge" />\r\n\t<meta http-equiv="Content-Type" content="text/html; charset=utf-8" />\r\n\t<meta http-equiv="pragma" content="no-cache"/>\r\n\t<meta http-equiv="Cache-Control" content="No-Cache"/>\r\n\t<title>Gsretail Site</title>\r\n\t<script type="text/javascript" src="/_ui/desktop/common/js/gsretail/jquery-1.11.2.js"></script>\r\n    <script type="text/javascript" src="/_ui/desktop/common/js/gsretail/ui.js"></script>\r\n    <script type="text/javascript" src="/_ui/desktop/common/js/gsretail/jPushMenu.js"></script>\r\n\t<script type="text/javascript" src="/_ui/desktop/common/js/gsretail/selectbox-min.js"></script>\r\n\t<link rel="stylesheet" type="text/css" href="/_ui/desktop/common/css/gsretail/common.css" />\r\n\r\n</head>\r\n<body>

In [3]:
#에러 상태 확인 (앞자리 4는 에러)
r.status_code

403

In [15]:
from bs4 import BeautifulSoup as BS
get_url = "https://gs25.gsretail.com/gscvs/ko/store-services/locations#;"

r = requests.get(get_url)

BS(r.text).find("form", id = 'CSRFForm')

<form action="/gscvs/ko/store-services/locations" id="CSRFForm" method="post"><input name="CSRFToken" type="hidden" value="d99b3130-1a36-47bb-b470-7bdaab339c3b"/>
</form>

In [14]:
from bs4 import BeautifulSoup as BS
get_url = "https://gs25.gsretail.com/gscvs/ko/store-services/locations#;"

r = requests.get(get_url)

csrf = BS(r.text).find("form", id = 'CSRFForm').find("input")['value']
#값이 매번 바뀌므로 예측 불가능
print(csrf)

14de30c9-079a-4643-8767-d4cc2f683053


In [24]:
from bs4 import BeautifulSoup as BS
#restfulAPI 주소 
url = "https://gs25.gsretail.com/gscvs/ko/store-services/locationList?CSRFToken={}"
#Session 접속 유지(재인증, 재로그인), 세션을 유지하고 싶으면 쿠키 사용 / CSRF 토큰 값을 유지하기 위해 with구문으로 세션 활용 
with requests.Session() as s:
    #CSRF토큰 값을 가져오기 위해 전체 주소 가져옴 
    get_url = "https://gs25.gsretail.com/gscvs/ko/store-services/locations#;"
    r = s.get(get_url)

    csrf = BS(r.text).find("form", id = 'CSRFForm').find("input")['value']

    r2 = s.post(url.format(csrf), data=payload)
    print(r2.text)

"{\"results\":[{\"offeringService\":[\"cafe25\",\"drug\",\"post\",\"withdrawal\",\"self_cook\",\"parcel_service\"],\"shopCode\":\"VDE68\",\"longs\":\"37.48189484\",\"address\":\"서울 강남구 논현로24길17(도곡2동 450-5)\",\"shopName\":\"GS25도곡STX점\",\"lat\":\"127.04437458\"},{\"offeringService\":[\"parcel_service\"],\"shopCode\":\"VFN73\",\"longs\":\"37.49026868\",\"address\":\"서울 강남구 도곡로132 (도곡동 553-1)\",\"shopName\":\"GS25도곡대박점\",\"lat\":\"127.03476909\"},{\"offeringService\":[\"cafe25\",\"post\",\"parcel_service\",\"spirit_wine\",\"fresh_ganghw\"],\"shopCode\":\"VFY23\",\"longs\":\"37.48990187\",\"address\":\"서울 강남구 남부순환로2803, 상가서관 1층 101,102,103호 (도곡동 91-5)\",\"shopName\":\"GS25도곡래미안점\",\"lat\":\"127.05066164\"},{\"offeringService\":[\"cafe25\",\"drug\",\"post\",\"parcel_service\"],\"shopCode\":\"V4W56\",\"longs\":\"37.48910588\",\"address\":\"서울 강남구 남부순환로365길56, 104호 (도곡동 895-4)\",\"shopName\":\"GS25도곡럭키본점\",\"lat\":\"127.04024578\"},{\"offeringService\":[\"cafe25\",\"instant\",\"drug\",\"post\

In [25]:
print(r2.json())

{"results":[{"offeringService":["cafe25","drug","post","withdrawal","self_cook","parcel_service"],"shopCode":"VDE68","longs":"37.48189484","address":"서울 강남구 논현로24길17(도곡2동 450-5)","shopName":"GS25도곡STX점","lat":"127.04437458"},{"offeringService":["parcel_service"],"shopCode":"VFN73","longs":"37.49026868","address":"서울 강남구 도곡로132 (도곡동 553-1)","shopName":"GS25도곡대박점","lat":"127.03476909"},{"offeringService":["cafe25","post","parcel_service","spirit_wine","fresh_ganghw"],"shopCode":"VFY23","longs":"37.48990187","address":"서울 강남구 남부순환로2803, 상가서관 1층 101,102,103호 (도곡동 91-5)","shopName":"GS25도곡래미안점","lat":"127.05066164"},{"offeringService":["cafe25","drug","post","parcel_service"],"shopCode":"V4W56","longs":"37.48910588","address":"서울 강남구 남부순환로365길56, 104호 (도곡동 895-4)","shopName":"GS25도곡럭키본점","lat":"127.04024578"},{"offeringService":["cafe25","instant","drug","post","parcel_service"],"shopCode":"VY612","longs":"37.4954324","address":"서울 강남구 선릉로225, 지하층 비101,102호  (도곡동 527-3, 도곡렉슬상가)","shopName":

In [26]:
BS(r.text).find("select", id = 'stb1')

<select class="select1" id="stb1" name="" onchange="fnSidoComboChange();" title="지역 선택">
<option value="">지역 선택</option>
<option value="11">서울시</option>
<option value="26">부산시</option>
<option value="27">대구시</option>
<option value="29">광주시</option>
<option value="28">인천시</option>
<option value="30">대전시</option>
<option value="31">울산시</option>
<option value="36">세종특별자치시</option>
<option value="41">경기도</option>
<option value="51">강원특별자치도</option>
<option value="44">충청남도</option>
<option value="43">충청북도</option>
<option value="48">경상남도</option>
<option value="47">경상북도</option>
<option value="46">전라남도</option>
<option value="52">전북특별자치도</option>
<option value="50">제주특별자치도</option>
</select>

In [30]:
BS(r.text).find("select", id = 'stb1').findAll("option")

[<option value="">지역 선택</option>,
 <option value="11">서울시</option>,
 <option value="26">부산시</option>,
 <option value="27">대구시</option>,
 <option value="29">광주시</option>,
 <option value="28">인천시</option>,
 <option value="30">대전시</option>,
 <option value="31">울산시</option>,
 <option value="36">세종특별자치시</option>,
 <option value="41">경기도</option>,
 <option value="51">강원특별자치도</option>,
 <option value="44">충청남도</option>,
 <option value="43">충청북도</option>,
 <option value="48">경상남도</option>,
 <option value="47">경상북도</option>,
 <option value="46">전라남도</option>,
 <option value="52">전북특별자치도</option>,
 <option value="50">제주특별자치도</option>]

In [34]:
#리스트 형식이니까 
for x in BS(r.text).find("select", id = 'stb1').findAll("option")[1:]:
    print(x.text)

서울시
부산시
대구시
광주시
인천시
대전시
울산시
세종특별자치시
경기도
강원특별자치도
충청남도
충청북도
경상남도
경상북도
전라남도
전북특별자치도
제주특별자치도


In [38]:
x

<option value="50">제주특별자치도</option>

In [37]:
for x in BS(r.text).find("select", id = 'stb1').findAll("option")[1:]:
    print(x.text, x['value'])

서울시 11
부산시 26
대구시 27
광주시 29
인천시 28
대전시 30
울산시 31
세종특별자치시 36
경기도 41
강원특별자치도 51
충청남도 44
충청북도 43
경상남도 48
경상북도 47
전라남도 46
전북특별자치도 52
제주특별자치도 50


In [41]:
sido = {}

for x in BS(r.text).find("select", id = 'stb1').findAll("option")[1:]:
    #print(x.text, x['value'])
    sido[x.text] = x['value']

#dictionary comprehension
#sido = {x.text : x['value'] for x in BS(r.text).find("select", id='stb1').findAll("option")[1:]}

In [42]:
sido

{'서울시': '11',
 '부산시': '26',
 '대구시': '27',
 '광주시': '29',
 '인천시': '28',
 '대전시': '30',
 '울산시': '31',
 '세종특별자치시': '36',
 '경기도': '41',
 '강원특별자치도': '51',
 '충청남도': '44',
 '충청북도': '43',
 '경상남도': '48',
 '경상북도': '47',
 '전라남도': '46',
 '전북특별자치도': '52',
 '제주특별자치도': '50'}

서울시 강남구 대치동에 있는 편의점은?

In [49]:
#서울11
#강남1168
#대치 11680106
from bs4 import BeautifulSoup as BS

payload['searchSido'] = 11
payload['searchGugun'] = 1168
payload['searchDong'] = 11680106

url = "https://gs25.gsretail.com/gscvs/ko/store-services/locationList?CSRFToken={}"

with requests.Session() as s:
    #CSRF토큰 값을 가져오기 위해 전체 주소 가져옴 
    get_url = "https://gs25.gsretail.com/gscvs/ko/store-services/locations#;"
    r = s.get(get_url)

    csrf = BS(r.text).find("form", id = 'CSRFForm').find("input")['value']

    r2 = s.post(url.format(csrf), data=payload)
    print(r2.json())

{"results":[{"shopCode":"V3G77","longs":"37.50502169","address":"서울 강남구 테헤란로416, 마사회선릉지사 7층 (대치동 890-8, 연봉빌딩)","shopName":"GS25R선릉7점","lat":"127.05179352"},{"offeringService":["cafe25","drug","post","withdrawal","potatoes","fish_shaped_bun"],"shopCode":"VQ181","longs":"37.50569924","address":"서울 강남구 삼성로434, 1층 (대치동 942-4, 쥬비스타워)","shopName":"GS25강남쥬비스점","lat":"127.05764377"},{"offeringService":["cafe25","instant","drug","post","withdrawal","parcel_service"],"shopCode":"V7N86","longs":"37.49561364","address":"서울 강남구 삼성로51길25, 104,105호 (대치동 612, 대치SK-VIEW아파트)","shopName":"GS25대치SK타운점","lat":"127.05955733"},{"offeringService":["cafe25","drug","post","withdrawal","parcel_service","potatoes","fish_shaped_bun"],"shopCode":"VJJ47","longs":"37.50408127","address":"서울 강남구 선릉로86길48 (대치4동 896-52, 동창빌딩)","shopName":"GS25대치골드점","lat":"127.05362636"},{"offeringService":["cafe25","instant","drug","post","parcel_service","potatoes","fish_shaped_bun"],"shopCode":"VO626","longs":"37.50688037","address":

In [127]:
data = eval(r2.json())['results']
data

[{'shopCode': 'V3G77',
  'longs': '37.50502169',
  'address': '서울 강남구 테헤란로416, 마사회선릉지사 7층 (대치동 890-8, 연봉빌딩)',
  'shopName': 'GS25R선릉7점',
  'lat': '127.05179352'},
 {'offeringService': ['cafe25',
   'drug',
   'post',
   'withdrawal',
   'potatoes',
   'fish_shaped_bun'],
  'shopCode': 'VQ181',
  'longs': '37.50569924',
  'address': '서울 강남구 삼성로434, 1층 (대치동 942-4, 쥬비스타워)',
  'shopName': 'GS25강남쥬비스점',
  'lat': '127.05764377'},
 {'offeringService': ['cafe25',
   'instant',
   'drug',
   'post',
   'withdrawal',
   'parcel_service'],
  'shopCode': 'V7N86',
  'longs': '37.49561364',
  'address': '서울 강남구 삼성로51길25, 104,105호 (대치동 612, 대치SK-VIEW아파트)',
  'shopName': 'GS25대치SK타운점',
  'lat': '127.05955733'},
 {'offeringService': ['cafe25',
   'drug',
   'post',
   'withdrawal',
   'parcel_service',
   'potatoes',
   'fish_shaped_bun'],
  'shopCode': 'VJJ47',
  'longs': '37.50408127',
  'address': '서울 강남구 선릉로86길48 (대치4동 896-52, 동창빌딩)',
  'shopName': 'GS25대치골드점',
  'lat': '127.05362636'},
 {'offering

In [47]:
sido.values()

dict_values(['11', '26', '27', '29', '28', '30', '31', '36', '41', '51', '44', '43', '48', '47', '46', '52', '50'])

In [126]:
#나 
import requests
url = "https://gs25.gsretail.com/gscvs/ko/gsapi/gis/searchGungu?&stb1={}&_=173128406335"
#dong = {}
#sido[x.text] = x['value']
for x in sido.values():
    r = requests.get(url.format(x))
    dong[x] = r.json()['result']

print(dong.values())

dict_values([[['1168', '강남구'], ['1174', '강동구'], ['1130', '강북구'], ['1150', '강서구'], ['1162', '관악구'], ['1121', '광진구'], ['1153', '구로구'], ['1154', '금천구'], ['1135', '노원구'], ['1132', '도봉구'], ['1123', '동대문구'], ['1159', '동작구'], ['1144', '마포구'], ['1141', '서대문구'], ['1165', '서초구'], ['1120', '성동구'], ['1129', '성북구'], ['1171', '송파구'], ['1147', '양천구'], ['1156', '영등포구'], ['1117', '용산구'], ['1138', '은평구'], ['1111', '종로구'], ['1114', '중구'], ['1126', '중랑구']], [['2644', '강서구'], ['2641', '금정구'], ['2671', '기장군'], ['2629', '남구'], ['2617', '동구'], ['2626', '동래구'], ['2623', '부산진구'], ['2632', '북구'], ['2653', '사상구'], ['2638', '사하구'], ['2614', '서구'], ['2650', '수영구'], ['2647', '연제구'], ['2620', '영도구'], ['2611', '중구'], ['2635', '해운대구']], [['2772', '군위군'], ['2720', '남구'], ['2729', '달서구'], ['2771', '달성군'], ['2714', '동구'], ['2723', '북구'], ['2717', '서구'], ['2726', '수성구'], ['2711', '중구']], [['2920', '광산구'], ['2915', '남구'], ['2911', '동구'], ['2917', '북구'], ['2914', '서구']], [['2871', '강화군'], ['2824', '계양구'], ['2820', '남동구'], ['

서울시에 있는 GS편의점은?

In [128]:
#서울11
#강남1168
#대치11680106
from bs4 import BeautifulSoup as BS

payload['searchSido'] = 11
payload['searchGugun'] = ''
payload['searchDong'] = ''

url = "https://gs25.gsretail.com/gscvs/ko/store-services/locationList?CSRFToken={}"

with requests.Session() as s:
    #CSRF토큰 값을 가져오기 위해 전체 주소 가져옴 
    get_url = "https://gs25.gsretail.com/gscvs/ko/store-services/locations#;"
    r = s.get(get_url)

    csrf = BS(r.text).find("form", id = 'CSRFForm').find("input")['value']

    r2 = s.post(url.format(csrf), data=payload)
    data = eval(r2.json())['results']
    print(data)

[{'offeringService': ['post', 'parcel_service'], 'shopCode': 'VQ037', 'longs': '37.52831065', 'address': '서울 양천구 목동서로159-1 (목1동 917-1, CBS방송국1층)', 'shopName': 'GS25CBS점', 'lat': '126.87486792'}, {'offeringService': ['cafe25', 'post', 'parcel_service'], 'shopCode': 'VO395', 'longs': '37.5783899', 'address': '서울 마포구 매봉산로75, 1층 107호 (상암동 1610)', 'shopName': 'GS25DDMC점', 'lat': '126.89294205'}, {'offeringService': ['cafe25', 'drug', 'post', 'parcel_service'], 'shopCode': 'VGP68', 'longs': '37.57410234', 'address': '서울 서대문구 가재울미래로2, 203동 101호 (남가좌동 385, 2단지)', 'shopName': 'GS25DMC가재울점', 'lat': '126.91639401'}, {'offeringService': ['cafe25', 'drug', 'post', 'parcel_service'], 'shopCode': 'VFP43', 'longs': '37.58474731', 'address': '서울 은평구 은평터널로27, 상가 105호, 106호 (수색동 189)', 'shopName': 'GS25DMC아트포레점', 'lat': '126.89830523'}, {'offeringService': ['cafe25', 'instant', 'drug', 'post', 'parcel_service', 'potatoes', 'cardiac_defi', 'spirit_wine'], 'shopCode': 'V9A48', 'longs': '37.50235508', 'addr

In [129]:
cnt = 0
for x in data:
    if x['address'].find("금천구") > -1:
        cnt += 1

cnt

97

In [130]:
#키, 벨류값이 나와있는 딕셔너리 값은 DataFrame으로 변환 가능
import pandas as pd
df = pd.DaaFrame(data)
df

offeringService shopCode        longs  \
0                                [post, parcel_service]    VQ037  37.52831065   
1                        [cafe25, post, parcel_service]    VO395   37.5783899   
2                  [cafe25, drug, post, parcel_service]    VGP68  37.57410234   
3                  [cafe25, drug, post, parcel_service]    VFP43  37.58474731   
4     [cafe25, instant, drug, post, parcel_service, ...    V9A48  37.50235508   
...                                                 ...      ...          ...   
3178                     [cafe25, drug, parcel_service]    VFQ46  37.60131235   
3179                                                NaN    V1999  37.54813528   
3180                                                NaN    V1880  37.56433789   
3181                                                NaN    V1882  37.50287602   
3182      [drug, post, withdrawal, tax, parcel_service]    VW993  37.59431984   

                                                address      shopName  \
0                서울 양천구 목동서로159-1 (목1동 917-1, CBS방송국1층)      GS25CBS점   
1                     서울 마포구 매봉산로75, 1층 107호 (상암동 1610)     GS25DDMC점   
2            서울 서대문구 가재울미래로2, 203동 101호 (남가좌동 385, 2단지)   GS25DMC가재울점   
3               서울 은평구 은평터널로27, 상가 105호, 106호 (수색동 189)  GS25DMC아트포레점   
4          서울 강남구 테헤란로223, 1층 101호 (역삼동 677-25, 큰길타워빌딩)    GS25DXLAB점   
...                                                 ...           ...   
3178         서울 은평구 통일로610, 상가동 109호 (녹번동 282, 힐스테이트녹번)  GS25힐스테이트녹번점   
3179                         서울 강서구 강서로251 (내발산동 723-9)      H&B우장산역점   
3180  서울 성동구 왕십리로지하 374, 207-02호  (하왕십리동 946-14, 상왕십리역)      S2상왕십리역점   
3181                 서울 동작구 현충로257, 431-02호 (동작동 327-1)        S4동작역점   
3182       서울 동대문구 경희대로23, 문화복지시설 101호 (회기동 1-5, 전면플라자)        경희프라자점   

               lat  
0     126.87486792  
1     126.89294205  
2     126.91639401  
3     126.89830523  
4     127.04069826  
...            ...  
3178  126.93606702  
3179  126.83601405  
3180  127.02961475  
3181   126.9802623  
3182  127.05231488  

[3183 rows x 6 columns]

In [131]:
df.head(2)

offeringService shopCode        longs  \
0          [post, parcel_service]    VQ037  37.52831065   
1  [cafe25, post, parcel_service]    VO395   37.5783899   

                                  address   shopName           lat  
0  서울 양천구 목동서로159-1 (목1동 917-1, CBS방송국1층)   GS25CBS점  126.87486792  
1       서울 마포구 매봉산로75, 1층 107호 (상암동 1610)  GS25DDMC점  126.89294205

In [132]:
df['address'].apply(lambda x : x.split())

0           [서울, 양천구, 목동서로159-1, (목1동, 917-1,, CBS방송국1층)]
1               [서울, 마포구, 매봉산로75,, 1층, 107호, (상암동, 1610)]
2       [서울, 서대문구, 가재울미래로2,, 203동, 101호, (남가좌동, 385,, ...
3        [서울, 은평구, 은평터널로27,, 상가, 105호,, 106호, (수색동, 189)]
4       [서울, 강남구, 테헤란로223,, 1층, 101호, (역삼동, 677-25,, 큰...
                              ...                        
3178    [서울, 은평구, 통일로610,, 상가동, 109호, (녹번동, 282,, 힐스테이...
3179                     [서울, 강서구, 강서로251, (내발산동, 723-9)]
3180    [서울, 성동구, 왕십리로지하, 374,, 207-02호, (하왕십리동, 946-1...
3181            [서울, 동작구, 현충로257,, 431-02호, (동작동, 327-1)]
3182    [서울, 동대문구, 경희대로23,, 문화복지시설, 101호, (회기동, 1-5,, ...
Name: address, Length: 3183, dtype: object

In [143]:
#칼럼 추가 
df['gu'] = df['address'].apply(lambda x : x.split()[1])

In [144]:
df[df['address'].duplicated()]

offeringService shopCode        longs  \
472   [toto, cafe25, instant, drug, post, withdrawal...    VDG88  37.46699742   
1464                                   [parcel_service]    V1960  37.51643968   
1465                     [parcel_service, cardiac_defi]    V1961  37.51643968   
1466                                   [parcel_service]    V1962  37.51643968   
1720                                     [cardiac_defi]    V9A15   37.5683032   
1721                                     [cardiac_defi]    V9A16   37.5683032   
1722                                                NaN    V9A36   37.5683032   
1723                                                NaN    V9A37   37.5683032   
1724                                                NaN    V9A38   37.5683032   
1725                                                NaN    V9A39   37.5683032   
1726                                                NaN    V9A40   37.5683032   
1727                                                NaN    V9A41   37.5683032   
1728                                                NaN    V9A42   37.5683032   
1729                                                NaN    V9A43   37.5683032   
1730                                                NaN    V9A44   37.5683032   
1731                                                NaN    V9A45   37.5683032   
1732                                                NaN    V9A46   37.5683032   
1734                                                NaN    V1992   37.5683032   
1735                                     [cardiac_defi]    V1995   37.5683032   
1736                                     [cardiac_defi]    V9A09   37.5683032   
1737                                     [cardiac_defi]    V9A10   37.5683032   
1738                                     [cardiac_defi]    V9A11   37.5683032   
1739                                     [cardiac_defi]    V9A12   37.5683032   
1740                                                NaN    V9A13   37.5683032   
1742             [cafe25, drug, potatoes, cardiac_defi]    V1203  37.56963416   
2488                                                NaN    V6W79  37.52134267   
2505                                   [parcel_service]    V1957  37.51643968   
2506                                   [parcel_service]    V1958  37.51643968   
2570                                       [drug, post]    VQ774  37.60953238   
2675                                     [cardiac_defi]    V1020  37.51643968   
2679                                   [parcel_service]    V1242  37.51643968   
2680                                   [parcel_service]    V1243  37.51643968   
2683                                   [parcel_service]    V1258  37.51643968   

                                         address         shopName  \
472              서울 관악구 대학길84, 1층,지층 (대학동 253-3)        GS25관악장원점   
1464                      서울 송파구 올림픽로25 (잠실동 10)         GS25보조3점   
1465                      서울 송파구 올림픽로25 (잠실동 10)         GS25보조4점   
1466                      서울 송파구 올림픽로25 (잠실동 10)         GS25보조6점   
1720                    서울 마포구 월드컵로240 (성산동 515)  GS25서울월드컵경기장11점   
1721                    서울 마포구 월드컵로240 (성산동 515)  GS25서울월드컵경기장12점   
1722                    서울 마포구 월드컵로240 (성산동 515)  GS25서울월드컵경기장13점   
1723                    서울 마포구 월드컵로240 (성산동 515)  GS25서울월드컵경기장14점   
1724                    서울 마포구 월드컵로240 (성산동 515)  GS25서울월드컵경기장15점   
1725                    서울 마포구 월드컵로240 (성산동 515)  GS25서울월드컵경기장16점   
1726                    서울 마포구 월드컵로240 (성산동 515)  GS25서울월드컵경기장17점   
1727                    서울 마포구 월드컵로240 (성산동 515)  GS25서울월드컵경기장18점   
1728                    서울 마포구 월드컵로240 (성산동 515)  GS25서울월드컵경기장19점   
1729                    서울 마포구 월드컵로240 (성산동 515)  GS25서울월드컵경기장20점   
1730                    서울 마포구 월드컵로240 (성산동 515)  GS25서울월드컵경기장21점   
1731                    서울 마포구 월드컵로240 (성산동 515)  GS25서울월드컵경기장22점   
1732                    서울 마포구 월드컵로240 (성산동 515)  GS25서울월드컵경기장23점   
1734                    서울 마포구 월드컵로240 (성산동

In [145]:
df[df[['address', 'shopName']].duplicated()]

offeringService shopCode        longs  \
2570    [drug, post]    VQ774  37.60953238   

                                         address    shopName           lat  \
2570  서울 성북구 오패산로84,  108호(하월곡동 225-6, 래미안월곡아파트)  GS25월곡래미안점  127.03599343   

       gu  
2570  성북구

In [147]:
df

offeringService shopCode        longs  \
0                                [post, parcel_service]    VQ037  37.52831065   
1                        [cafe25, post, parcel_service]    VO395   37.5783899   
2                  [cafe25, drug, post, parcel_service]    VGP68  37.57410234   
3                  [cafe25, drug, post, parcel_service]    VFP43  37.58474731   
4     [cafe25, instant, drug, post, parcel_service, ...    V9A48  37.50235508   
...                                                 ...      ...          ...   
3178                     [cafe25, drug, parcel_service]    VFQ46  37.60131235   
3179                                                NaN    V1999  37.54813528   
3180                                                NaN    V1880  37.56433789   
3181                                                NaN    V1882  37.50287602   
3182      [drug, post, withdrawal, tax, parcel_service]    VW993  37.59431984   

                                                address      shopName  \
0                서울 양천구 목동서로159-1 (목1동 917-1, CBS방송국1층)      GS25CBS점   
1                     서울 마포구 매봉산로75, 1층 107호 (상암동 1610)     GS25DDMC점   
2            서울 서대문구 가재울미래로2, 203동 101호 (남가좌동 385, 2단지)   GS25DMC가재울점   
3               서울 은평구 은평터널로27, 상가 105호, 106호 (수색동 189)  GS25DMC아트포레점   
4          서울 강남구 테헤란로223, 1층 101호 (역삼동 677-25, 큰길타워빌딩)    GS25DXLAB점   
...                                                 ...           ...   
3178         서울 은평구 통일로610, 상가동 109호 (녹번동 282, 힐스테이트녹번)  GS25힐스테이트녹번점   
3179                         서울 강서구 강서로251 (내발산동 723-9)      H&B우장산역점   
3180  서울 성동구 왕십리로지하 374, 207-02호  (하왕십리동 946-14, 상왕십리역)      S2상왕십리역점   
3181                 서울 동작구 현충로257, 431-02호 (동작동 327-1)        S4동작역점   
3182       서울 동대문구 경희대로23, 문화복지시설 101호 (회기동 1-5, 전면플라자)        경희프라자점   

               lat    gu  
0     126.87486792   양천구  
1     126.89294205   마포구  
2     126.91639401  서대문구  
3     126.89830523   은평구  
4     127.04069826   강남구  
...            ...   ...  
3178  126.93606702   은평구  
3179  126.83601405   강서구  
3180  127.02961475   성동구  
3181   126.9802623   동작구  
3182  127.05231488  동대문구  

[3183 rows x 7 columns]

In [149]:
#시리즈형태 이를 데이터프레임이라는 껍데기 씌우고 싶다면 []
df.groupby(['gu'])['address'].count()

gu
강남구     274
강동구     119
강북구      79
강서구     187
관악구     157
광진구     104
구로구     127
금천구      97
노원구     129
도봉구      82
동대문구    116
동작구     117
마포구     192
서대문구     93
서초구     146
성동구      85
성북구     109
송파구     183
양천구      93
영등포구    177
용산구      84
은평구     133
종로구      76
중구      107
중랑구     117
Name: address, dtype: int64

In [148]:
df.groupby(['gu'])[['address']].count().sort_values(by=['address'], ascending=False)

address
gu           
강남구       274
마포구       192
강서구       187
송파구       183
영등포구      177
관악구       157
서초구       146
은평구       133
노원구       129
구로구       127
강동구       119
동작구       117
중랑구       117
동대문구      116
성북구       109
중구        107
광진구       104
금천구        97
서대문구       93
양천구        93
성동구        85
용산구        84
도봉구        82
강북구        79
종로구        76

In [155]:
df.loc[df['offeringService'].notnull()]

offeringService shopCode        longs  \
0                                [post, parcel_service]    VQ037  37.52831065   
1                        [cafe25, post, parcel_service]    VO395   37.5783899   
2                  [cafe25, drug, post, parcel_service]    VGP68  37.57410234   
3                  [cafe25, drug, post, parcel_service]    VFP43  37.58474731   
4     [cafe25, instant, drug, post, parcel_service, ...    V9A48  37.50235508   
...                                                 ...      ...          ...   
3175               [cafe25, drug, post, parcel_service]    V4Z23   37.5048858   
3176  [cafe25, post, atm, withdrawal, smart_atm, par...    V4R52  37.50315589   
3177   [cafe25, drug, post, withdrawal, parcel_service]    VDY57  37.54179215   
3178                     [cafe25, drug, parcel_service]    VFQ46  37.60131235   
3182      [drug, post, withdrawal, tax, parcel_service]    VW993  37.59431984   

                                                address      shopName  \
0                서울 양천구 목동서로159-1 (목1동 917-1, CBS방송국1층)      GS25CBS점   
1                     서울 마포구 매봉산로75, 1층 107호 (상암동 1610)     GS25DDMC점   
2            서울 서대문구 가재울미래로2, 203동 101호 (남가좌동 385, 2단지)   GS25DMC가재울점   
3               서울 은평구 은평터널로27, 상가 105호, 106호 (수색동 189)  GS25DMC아트포레점   
4          서울 강남구 테헤란로223, 1층 101호 (역삼동 677-25, 큰길타워빌딩)    GS25DXLAB점   
...                                                 ...           ...   
3175       서울 동작구 흑석한강로27 (흑석동 336, 한강푸르지오상가106동B205gh)   GS25흑석푸르지오점   
3176           서울 동작구 흑석한강로27, 상가D동 B303,304호 (흑석동 336)     GS25흑석한강점   
3177  서울 강동구 올림픽로78길30, 102동 상가 101호 (천호동 437-5, 힐데스...    GS25힐데스하임점   
3178         서울 은평구 통일로610, 상가동 109호 (녹번동 282, 힐스테이트녹번)  GS25힐스테이트녹번점   
3182       서울 동대문구 경희대로23, 문화복지시설 101호 (회기동 1-5, 전면플라자)        경희프라자점   

               lat    gu  
0     126.87486792   양천구  
1     126.89294205   마포구  
2     126.91639401  서대문구  
3     126.89830523   은평구  
4     127.04069826   강남구  
...            ...   ...  
3175  126.96580307   동작구  
3176  126.96478641   동작구  
3177   127.1263527   강동구  
3178  126.93606702   은평구  
3182  127.05231488  동대문구  

[3079 rows x 7 columns]

In [170]:
tmp = []
df.loc[df['offeringService'].notnull(), 'offeringService'].apply(lambda x : tmp.extend(x))

0       None
1       None
2       None
3       None
4       None
        ... 
3175    None
3176    None
3177    None
3178    None
3182    None
Name: offeringService, Length: 3079, dtype: object

In [167]:
tmp = df.loc[df['offeringService'].notnull(), 'offeringService'].apply(lambda x : ''.join(x))
tmp

0                                      postparcel_service
1                                cafe25postparcel_service
2                            cafe25drugpostparcel_service
3                            cafe25drugpostparcel_service
4       cafe25instantdrugpostparcel_servicepotatoescar...
                              ...                        
3175                         cafe25drugpostparcel_service
3176    cafe25postatmwithdrawalsmart_atmparcel_service...
3177               cafe25drugpostwithdrawalparcel_service
3178                             cafe25drugparcel_service
3182                  drugpostwithdrawaltaxparcel_service
Name: offeringService, Length: 3079, dtype: object

In [171]:
set(tmp)

{'atm',
 'cafe25',
 'cardiac_defi',
 'delivery_service',
 'drug',
 'fish_shaped_bun',
 'fresh_ganghw',
 'gopizza',
 'instant',
 'parcel_service',
 'post',
 'potatoes',
 'self_cook',
 'smart_atm',
 'spirit_wine',
 'tax',
 'toto',
 'withdrawal'}

In [172]:
tmp

['post',
 'parcel_service',
 'cafe25',
 'post',
 'parcel_service',
 'cafe25',
 'drug',
 'post',
 'parcel_service',
 'cafe25',
 'drug',
 'post',
 'parcel_service',
 'cafe25',
 'instant',
 'drug',
 'post',
 'parcel_service',
 'potatoes',
 'cardiac_defi',
 'spirit_wine',
 'drug',
 'withdrawal',
 'drug',
 'post',
 'withdrawal',
 'cafe25',
 'instant',
 'drug',
 'post',
 'atm',
 'withdrawal',
 'smart_atm',
 'self_cook',
 'potatoes',
 'fish_shaped_bun',
 'cafe25',
 'drug',
 'post',
 'atm',
 'withdrawal',
 'smart_atm',
 'self_cook',
 'potatoes',
 'fish_shaped_bun',
 'post',
 'parcel_service',
 'cafe25',
 'instant',
 'drug',
 'post',
 'withdrawal',
 'parcel_service',
 'potatoes',
 'fish_shaped_bun',
 'cafe25',
 'post',
 'parcel_service',
 'post',
 'spirit_wine',
 'post',
 'parcel_service',
 'cafe25',
 'post',
 'cafe25',
 'cafe25',
 'cafe25',
 'cafe25',
 'cafe25',
 'cafe25',
 'cafe25',
 'cafe25',
 'cafe25',
 'cafe25',
 'potatoes',
 'fish_shaped_bun',
 'cafe25',
 'potatoes',
 'fish_shaped_bun',
 

In [173]:
service = list(set(tmp))
service

['cardiac_defi',
 'spirit_wine',
 'drug',
 'delivery_service',
 'withdrawal',
 'self_cook',
 'fresh_ganghw',
 'toto',
 'instant',
 'fish_shaped_bun',
 'cafe25',
 'potatoes',
 'tax',
 'atm',
 'gopizza',
 'parcel_service',
 'post',
 'smart_atm']

In [176]:
df.loc[df['offeringService'].notnull(), 'offeringService'].apply(lambda x : 1 if 'cardiac_defi' in x else 0)

0       0
1       0
2       0
3       0
4       1
       ..
3175    0
3176    0
3177    0
3178    0
3182    0
Name: offeringService, Length: 3079, dtype: int64

In [180]:
for serv in service:
     df.loc[df['offeringService'].notnull(), serv] = \
    df.loc[df['offeringService'].notnull(), 'offeringService'].apply(lambda x : True if serv in x else False)

In [181]:
df

offeringService shopCode        longs  \
0                                [post, parcel_service]    VQ037  37.52831065   
1                        [cafe25, post, parcel_service]    VO395   37.5783899   
2                  [cafe25, drug, post, parcel_service]    VGP68  37.57410234   
3                  [cafe25, drug, post, parcel_service]    VFP43  37.58474731   
4     [cafe25, instant, drug, post, parcel_service, ...    V9A48  37.50235508   
...                                                 ...      ...          ...   
3178                     [cafe25, drug, parcel_service]    VFQ46  37.60131235   
3179                                                NaN    V1999  37.54813528   
3180                                                NaN    V1880  37.56433789   
3181                                                NaN    V1882  37.50287602   
3182      [drug, post, withdrawal, tax, parcel_service]    VW993  37.59431984   

                                                address      shopName  \
0                서울 양천구 목동서로159-1 (목1동 917-1, CBS방송국1층)      GS25CBS점   
1                     서울 마포구 매봉산로75, 1층 107호 (상암동 1610)     GS25DDMC점   
2            서울 서대문구 가재울미래로2, 203동 101호 (남가좌동 385, 2단지)   GS25DMC가재울점   
3               서울 은평구 은평터널로27, 상가 105호, 106호 (수색동 189)  GS25DMC아트포레점   
4          서울 강남구 테헤란로223, 1층 101호 (역삼동 677-25, 큰길타워빌딩)    GS25DXLAB점   
...                                                 ...           ...   
3178         서울 은평구 통일로610, 상가동 109호 (녹번동 282, 힐스테이트녹번)  GS25힐스테이트녹번점   
3179                         서울 강서구 강서로251 (내발산동 723-9)      H&B우장산역점   
3180  서울 성동구 왕십리로지하 374, 207-02호  (하왕십리동 946-14, 상왕십리역)      S2상왕십리역점   
3181                 서울 동작구 현충로257, 431-02호 (동작동 327-1)        S4동작역점   
3182       서울 동대문구 경희대로23, 문화복지시설 101호 (회기동 1-5, 전면플라자)        경희프라자점   

               lat    gu  serv cardiac_defi spirit_wine  ... instant  \
0     126.87486792   양천구   0.0        False       False  ...   False   
1     126.89294205   마포구   0.0        False       False  ...   False   
2     126.91639401  서대문구   0.0        False       False  ...   False   
3     126.89830523   은평구   0.0        False       False  ...   False   
4     127.04069826   강남구   0.0         True        True  ...    True   
...            ...   ...   ...          ...         ...  ...     ...   
3178  126.93606702   은평구   0.0        False       False  ...   False   
3179  126.83601405   강서구   NaN          NaN         NaN  ...     NaN   
3180  127.02961475   성동구   NaN          NaN         NaN  ...     NaN   
3181   126.9802623   동작구   NaN          NaN         NaN  ...     NaN   
3182  127.05231488  동대문구   0.0        False       False  ...   False   

     fish_shaped_bun cafe25 potatoes    tax    atm gopizza parcel_service  \
0              False  False    False  False  False   False           True   
1              False   True    False  False  False   False           True   
2              False   True    False  False  False   False           True   
3              False   True    False  False  False   False           True   
4              False   True     True  False  False   False           True   
...              ...    ...      ...    ...    ...     ...            ...   
3178           False   True    False  False  False   False           True   
3179             NaN    NaN      NaN    NaN    NaN     NaN            NaN   
3180             NaN    NaN      NaN    NaN    NaN     NaN            NaN   
3181             NaN    NaN      NaN    NaN    NaN     NaN            NaN   
3182           False  False    False   True  False   False           True   

       post smart_atm  
0      True     False  
1      True     False  
2      True     False  
3      True     False  
4      True     False  
...     ...       ...  
3178  False     False  
3179    NaN       NaN  
3180    NaN       NaN  
3181    NaN       NaN  
3182   True     False  

[3183 rows x 26 columns]

In [182]:
df[(df.cafe25 == True)]

offeringService shopCode        longs  \
1                        [cafe25, post, parcel_service]    VO395   37.5783899   
2                  [cafe25, drug, post, parcel_service]    VGP68  37.57410234   
3                  [cafe25, drug, post, parcel_service]    VFP43  37.58474731   
4     [cafe25, instant, drug, post, parcel_service, ...    V9A48  37.50235508   
7     [cafe25, instant, drug, post, atm, withdrawal,...    VI465  37.51607005   
...                                                 ...      ...          ...   
3174  [cafe25, drug, post, parcel_service, potatoes,...    VGD48  37.50436274   
3175               [cafe25, drug, post, parcel_service]    V4Z23   37.5048858   
3176  [cafe25, post, atm, withdrawal, smart_atm, par...    V4R52  37.50315589   
3177   [cafe25, drug, post, withdrawal, parcel_service]    VDY57  37.54179215   
3178                     [cafe25, drug, parcel_service]    VFQ46  37.60131235   

                                                address      shopName  \
1                     서울 마포구 매봉산로75, 1층 107호 (상암동 1610)     GS25DDMC점   
2            서울 서대문구 가재울미래로2, 203동 101호 (남가좌동 385, 2단지)   GS25DMC가재울점   
3               서울 은평구 은평터널로27, 상가 105호, 106호 (수색동 189)  GS25DMC아트포레점   
4          서울 강남구 테헤란로223, 1층 101호 (역삼동 677-25, 큰길타워빌딩)    GS25DXLAB점   
7                      서울 서초구 나루터로83 (잠원동 13-6, 남서울주유소)   GS25G신사남서울점   
...                                                 ...           ...   
3174    서울 동작구 서달로123, 롯데캐슬에듀포레 단지내상가 1층 102호 (흑석동 340)     GS25흑석캐슬점   
3175       서울 동작구 흑석한강로27 (흑석동 336, 한강푸르지오상가106동B205gh)   GS25흑석푸르지오점   
3176           서울 동작구 흑석한강로27, 상가D동 B303,304호 (흑석동 336)     GS25흑석한강점   
3177  서울 강동구 올림픽로78길30, 102동 상가 101호 (천호동 437-5, 힐데스...    GS25힐데스하임점   
3178         서울 은평구 통일로610, 상가동 109호 (녹번동 282, 힐스테이트녹번)  GS25힐스테이트녹번점   

               lat    gu  serv cardiac_defi spirit_wine  ... instant  \
1     126.89294205   마포구   0.0        False       False  ...   False   
2     126.91639401  서대문구   0.0        False       False  ...   False   
3     126.89830523   은평구   0.0        False       False  ...   False   
4     127.04069826   강남구   0.0         True        True  ...    True   
7     127.01887155   서초구   1.0        False       False  ...    True   
...            ...   ...   ...          ...         ...  ...     ...   
3174  126.96061891   동작구   0.0        False       False  ...   False   
3175  126.96580307   동작구   0.0        False       False  ...   False   
3176  126.96478641   동작구   1.0        False       False  ...   False   
3177   127.1263527   강동구   0.0        False       False  ...   False   
3178  126.93606702   은평구   0.0        False       False  ...   False   

     fish_shaped_bun cafe25 potatoes    tax    atm gopizza parcel_service  \
1              False   True    False  False  False   False           True   
2              False   True    False  False  False   False           True   
3              False   True    False  False  False   False           True   
4              False   True     True  False  False   False           True   
7               True   True     True  False   True   False          False   
...              ...    ...      ...    ...    ...     ...            ...   
3174            True   True     True  False  False   False           True   
3175           False   True    False  False  False   False           True   
3176            True   True     True  False   True   False           True   
3177           False   True    False  False  False   False           True   
3178           False   True    False  False  False   False           True   

       post smart_atm  
1      True     False  
2      True     False  
3      True     False  
4      True     False  
7      True      True  
...     ...       ...  
3174   True     False  
3175   True     False  
3176   True      True  
3177   True     False  
3178  False     False  

[2575 rows x 26 columns]

In [183]:
df[(df.cafe25 == True) & (df.gu == '금천구')]

offeringService shopCode        longs  \
106                 [cafe25, potatoes, fish_shaped_bun]    V2B55  37.48228276   
181   [cafe25, drug, post, atm, withdrawal, smart_at...    V5682  37.48035526   
186          [cafe25, post, withdrawal, parcel_service]    V6Y85  37.46791396   
187           [cafe25, post, self_cook, parcel_service]    VM252   37.4718633   
188                            [cafe25, parcel_service]    VW942  37.47968438   
...                                                 ...      ...          ...   
2011  [cafe25, instant, drug, post, withdrawal, parc...    VEP56  37.45548154   
2012               [cafe25, drug, post, parcel_service]    VHV73  37.44880625   
2608  [cafe25, instant, drug, post, parcel_service, ...    VEZ52  37.45233204   
3002  [cafe25, drug, post, atm, withdrawal, smart_at...    V8W97  37.47564006   
3080  [cafe25, post, parcel_service, potatoes, fish_...    V8F87  37.46227568   

                                                address        shopName  \
106   서울 금천구 벚꽃로309, 7호선 가산디지털단지역 내 상가 3002 (가산동 468-4)  GS25S가산디지털단지역점   
181           서울 금천구 벚꽃로286,  1층 107호(가산동 60-15, 리더스타워)       GS25가리봉역점   
186                          서울 금천구 가산디지털1로25 (가산동 670)       GS25가산대륭점   
187                        서울 금천구 가산로3길113(독산1동 335-14)       GS25가산두산점   
188      서울 금천구 서부샛길606, 107호 (가산동 543-1, 대성디폴리스지식산업센터)     GS25가산디폴리스점   
...                                                 ...             ...   
2011                    서울 금천구 독산로25길35, 1층 (시흥동 878-9)       GS25시흥초교점   
2012            서울 금천구 금하로30길34, 상가 1층 (시흥동 268-46, 단지)      GS25시흥탑스빌점   
2608                          서울 금천구 독산로56 (시흥동 837-38)    GS25은행나무사거리점   
3002             서울 금천구 가산디지털1로119,  A동 103호(가산동 345-9)       GS25트윈테크점   
3080           서울 금천구 벚꽃로73, 상가동 110호, 111호 (독산동 711-2)      GS25현대홈타운점   

               lat   gu  serv cardiac_defi spirit_wine  ... instant  \
106   126.88218427  금천구   0.0        False       False  ...   False   
181   126.88416901  금천구   1.0        False       False  ...   False   
186   126.88630966  금천구   0.0        False       False  ...   False   
187   126.88947305  금천구   0.0        False       False  ...   False   
188   126.87707858  금천구   0.0        False       False  ...   False   
...            ...  ...   ...          ...         ...  ...     ...   
2011  126.90387766  금천구   0.0        False       False  ...    True   
2012   126.9157628  금천구   0.0        False       False  ...   False   
2608   126.9062745  금천구   0.0        False        True  ...    True   
3002  126.88292765  금천구   1.0        False       False  ...   False   
3080  126.89038352  금천구   0.0        False       False  ...   False   

     fish_shaped_bun cafe25 potatoes    tax    atm gopizza parcel_service  \
106             True   True     True  False  False   False          False   
181            False   True    False  False   True   False           True   
186            False   True    False  False  False   False           True   
187            False   True    False  False  False   False           True   
188            False   True    False  False  False   False           True   
...              ...    ...      ...    ...    ...     ...            ...   
2011           False   True    False  False  False   False           True   
2012           False   True    False  False  False   False           True   
2608           False   True    False  False  False   False           True   
3002            True   True    False  False   True   False           True   
3080            True   True     True  False  False   False           True   

       post smart_atm  
106   False     False  
181    True      True  
186    True     False  
187    True     False  
188   False     False  
...     ...       ...  
2011   True     False  
2012   True     False  
2608   True     False  
3002   True      True  
3080   True     False  

[66 rows x 26 columns]

In [185]:
df.columns

Index(['offeringService', 'shopCode', 'longs', 'address', 'shopName', 'lat',
       'gu', 'serv', 'cardiac_defi', 'spirit_wine', 'drug', 'delivery_service',
       'withdrawal', 'self_cook', 'fresh_ganghw', 'toto', 'instant',
       'fish_shaped_bun', 'cafe25', 'potatoes', 'tax', 'atm', 'gopizza',
       'parcel_service', 'post', 'smart_atm'],
      dtype='object')

In [191]:
gs_df = df[['shopName', 'shopCode', 'longs', 'lat', 'address', 'gu',
        'cafe25', 'post', 'potatoes', 'cardiac_defi', 'smart_atm',
       'fish_shaped_bun', 'instant', 'gopizza', 'drug', 'fresh_ganghw', 'tax',
       'toto', 'spirit_wine', 'withdrawal', 'self_cook', 'delivery_service',
       'parcel_service', 'atm']].copy()

In [192]:
gs_df

shopName shopCode        longs           lat  \
0         GS25CBS점    VQ037  37.52831065  126.87486792   
1        GS25DDMC점    VO395   37.5783899  126.89294205   
2      GS25DMC가재울점    VGP68  37.57410234  126.91639401   
3     GS25DMC아트포레점    VFP43  37.58474731  126.89830523   
4       GS25DXLAB점    V9A48  37.50235508  127.04069826   
...            ...      ...          ...           ...   
3178  GS25힐스테이트녹번점    VFQ46  37.60131235  126.93606702   
3179      H&B우장산역점    V1999  37.54813528  126.83601405   
3180      S2상왕십리역점    V1880  37.56433789  127.02961475   
3181        S4동작역점    V1882  37.50287602   126.9802623   
3182        경희프라자점    VW993  37.59431984  127.05231488   

                                                address    gu cafe25   post  \
0                서울 양천구 목동서로159-1 (목1동 917-1, CBS방송국1층)   양천구  False   True   
1                     서울 마포구 매봉산로75, 1층 107호 (상암동 1610)   마포구   True   True   
2            서울 서대문구 가재울미래로2, 203동 101호 (남가좌동 385, 2단지)  서대문구   True   True   
3               서울 은평구 은평터널로27, 상가 105호, 106호 (수색동 189)   은평구   True   True   
4          서울 강남구 테헤란로223, 1층 101호 (역삼동 677-25, 큰길타워빌딩)   강남구   True   True   
...                                                 ...   ...    ...    ...   
3178         서울 은평구 통일로610, 상가동 109호 (녹번동 282, 힐스테이트녹번)   은평구   True  False   
3179                         서울 강서구 강서로251 (내발산동 723-9)   강서구    NaN    NaN   
3180  서울 성동구 왕십리로지하 374, 207-02호  (하왕십리동 946-14, 상왕십리역)   성동구    NaN    NaN   
3181                 서울 동작구 현충로257, 431-02호 (동작동 327-1)   동작구    NaN    NaN   
3182       서울 동대문구 경희대로23, 문화복지시설 101호 (회기동 1-5, 전면플라자)  동대문구  False   True   

     potatoes cardiac_defi  ...   drug fresh_ganghw    tax   toto spirit_wine  \
0       False        False  ...  False        False  False  False       False   
1       False        False  ...  False        False  False  False       False   
2       False        False  ...   True        False  False  False       False   
3       False        False  ...   True        False  False  False       False   
4        True         True  ...   True        False  False  False        True   
...       ...          ...  ...    ...          ...    ...    ...         ...   
3178    False        False  ...   True        False  False  False       False   
3179      NaN          NaN  ...    NaN          NaN    NaN    NaN         NaN   
3180      NaN          NaN  ...    NaN          NaN    NaN    NaN         NaN   
3181      NaN          NaN  ...    NaN          NaN    NaN    NaN         NaN   
3182    False        False  ...   True        False   True  False       False   

     withdrawal self_cook delivery_service parcel_service    atm  
0         False     False            False           True  False  
1         False     False            False           True  False  
2         False     False            False           True  False  
3         False     False            False           True  False  
4         False     False            False           True  False  
...         ...       ...              ...            ...    ...  
3178      False     False            False           True  False  
3179        NaN       NaN              NaN            NaN    NaN  
3180        NaN       NaN              NaN            NaN    NaN  
3181        NaN       NaN              NaN            NaN    NaN  
3182       True     False            False           True  False  

[3183 rows x 24 columns]

In [193]:
gs_df['shopCode'].unique().size

3183

In [194]:
gs_df.shape

(3183, 24)

DB에 GS25 테이블 적재

In [195]:
import MySQLdb

con = MySQLdb.connect(host='localhost', user='encore', password='1234', db='encore')
cursor = con.cursor()

In [199]:
cursor.execute("""CREATE TABLE GS25 (
    shopName VARCHAR(50) DEFAULT NULL,
    shopCode VARCHAR(50) DEFAULT NULL,
    longs FLOAT DEFAULT NULL,
    lat FLOAT DEFAULT NULL,
    address VARCHAR(100) DEFAULT NULL,
    gu VARCHAR(50) DEFAULT NULL,
    cafe25 BOOLEAN DEFAULT NULL,
    post BOOLEAN DEFAULT NULL,
    potatoes BOOLEAN DEFAULT NULL,
    cardiac_defi BOOLEAN DEFAULT NULL,
    smart_atm BOOLEAN DEFAULT NULL,
    fish_shaped_bun BOOLEAN DEFAULT NULL,
    instant BOOLEAN DEFAULT NULL,
    gopizza BOOLEAN DEFAULT NULL,
    drug BOOLEAN DEFAULT NULL,
    fresh_ganghw BOOLEAN DEFAULT NULL,
    tax BOOLEAN DEFAULT NULL,
    toto BOOLEAN DEFAULT NULL,
    spirit_wine BOOLEAN DEFAULT NULL,
    withdrawal BOOLEAN DEFAULT NULL,
    self_cook BOOLEAN DEFAULT NULL,
    delivery_service BOOLEAN DEFAULT NULL,
    parcel_service BOOLEAN DEFAULT NULL,
    atm BOOLEAN DEFAULT NULL
)
""")


0

In [200]:
con.commit()

In [201]:
#gs_df.to_sql("GS25", index = False, if_exists = 'append', con=con)

gs_df.fillna("", inplace=True)

In [202]:
sql = "Insert into GS25 values (%s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s, %s)"


In [203]:
for idx, data in  gs_df.iterrows():
    #print(data)
    cursor.execute(sql, [None if x == '' else x for x in data.tolist()])

con.commit()

CU 데이터

In [221]:
cu_url = "https://www.pocketcu.co.kr/api/store/search/list"
#147까지 존재 
cu_payload = {"firstRowNum" : "1",
"searchWord": "서울"}

head = {"user-agent":
"Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/130.0.0.0 Safari/537.36"}

r = requests.post(cu_url, json=cu_payload, headers=head)

r.text

'{"storeCnt":0,"storeList":[{"storeCd":"49556","storeNm":"E홍성휴게소서울점","fcCd":null,"slcCd":null,"hangCd":"44","bumunCd":null,"teamCd":null,"scCd":null,"openYmd":"20240530","closeYmd":null,"storeOwnerNm":null,"juminNo":null,"storeTelNo":null,"storeSaupNo":null,"posId":null,"provId":null,"unyoungId":null,"useYn":"Y","applYmd":"20240605","oldStoreCd":null,"newStoreCd":null,"fcType2":null,"hangCd1":null,"hangCd2":"44800","hangCd3":null,"zipNo":"32209","storeAddr1":null,"storeAddr2":null,"doroZipNo":"32209","doroStoreAddr1":null,"doroStoreAddr2":null,"latVal":36.553295,"longVal":126.581863,"preStoreCd":null,"hour24Yn":"N","friedYn":"N","bakeryYn":"N","coffeeYn":"N","lottoYn":"N","totoYn":"N","atmYn":"N","storeDscr":null,"deliveryYn":"N","jumpoMultiDeviceYn":"N","jumpoPosCashYn":"N","jumpoBatteryYn":"N","jumpoDelivYn":"N","jumpoPickYn":"N","carpickYn":"N","reserveYn":"N","cookYn":"N","wineYn":"N","medicineYn":"N","tpiratesYn":"N","pickNYn":"N","namaneYn":"N","printingBoxYn":"N","deliveryPickYn

In [207]:
r.json()

{'storeCnt': 0,
 'storeList': [{'storeCd': '49556',
   'storeNm': 'E홍성휴게소서울점',
   'fcCd': None,
   'slcCd': None,
   'hangCd': '44',
   'bumunCd': None,
   'teamCd': None,
   'scCd': None,
   'openYmd': '20240530',
   'closeYmd': None,
   'storeOwnerNm': None,
   'juminNo': None,
   'storeTelNo': None,
   'storeSaupNo': None,
   'posId': None,
   'provId': None,
   'unyoungId': None,
   'useYn': 'Y',
   'applYmd': '20240605',
   'oldStoreCd': None,
   'newStoreCd': None,
   'fcType2': None,
   'hangCd1': None,
   'hangCd2': '44800',
   'hangCd3': None,
   'zipNo': '32209',
   'storeAddr1': None,
   'storeAddr2': None,
   'doroZipNo': '32209',
   'doroStoreAddr1': None,
   'doroStoreAddr2': None,
   'latVal': 36.553295,
   'longVal': 126.581863,
   'preStoreCd': None,
   'hour24Yn': 'N',
   'friedYn': 'N',
   'bakeryYn': 'N',
   'coffeeYn': 'N',
   'lottoYn': 'N',
   'totoYn': 'N',
   'atmYn': 'N',
   'storeDscr': None,
   'deliveryYn': 'N',
   'jumpoMultiDeviceYn': 'N',
   'jumpoPosCas

In [208]:
r.json()['storeList']

[{'storeCd': '49556',
  'storeNm': 'E홍성휴게소서울점',
  'fcCd': None,
  'slcCd': None,
  'hangCd': '44',
  'bumunCd': None,
  'teamCd': None,
  'scCd': None,
  'openYmd': '20240530',
  'closeYmd': None,
  'storeOwnerNm': None,
  'juminNo': None,
  'storeTelNo': None,
  'storeSaupNo': None,
  'posId': None,
  'provId': None,
  'unyoungId': None,
  'useYn': 'Y',
  'applYmd': '20240605',
  'oldStoreCd': None,
  'newStoreCd': None,
  'fcType2': None,
  'hangCd1': None,
  'hangCd2': '44800',
  'hangCd3': None,
  'zipNo': '32209',
  'storeAddr1': None,
  'storeAddr2': None,
  'doroZipNo': '32209',
  'doroStoreAddr1': None,
  'doroStoreAddr2': None,
  'latVal': 36.553295,
  'longVal': 126.581863,
  'preStoreCd': None,
  'hour24Yn': 'N',
  'friedYn': 'N',
  'bakeryYn': 'N',
  'coffeeYn': 'N',
  'lottoYn': 'N',
  'totoYn': 'N',
  'atmYn': 'N',
  'storeDscr': None,
  'deliveryYn': 'N',
  'jumpoMultiDeviceYn': 'N',
  'jumpoPosCashYn': 'N',
  'jumpoBatteryYn': 'N',
  'jumpoDelivYn': 'N',
  'jumpoPickYn'

In [222]:
cu_list = list()

for x in range(0, 148):
    cu_payload['firstRowNum'] = x
    r = requests.post(cu_url, json=cu_payload, headers=head)
    cu_list.extend(r.json()['storeList'])
                   
#2892
#r.json()['storeList'].__len__()

In [223]:
len(cu_list)

2959

In [244]:
cu_list

[{'storeCd': '45047',
  'storeNm': '419사거리점',
  'fcCd': None,
  'slcCd': None,
  'hangCd': '11',
  'bumunCd': None,
  'teamCd': None,
  'scCd': None,
  'openYmd': '20230110',
  'closeYmd': None,
  'storeOwnerNm': None,
  'juminNo': None,
  'storeTelNo': None,
  'storeSaupNo': None,
  'posId': None,
  'provId': None,
  'unyoungId': None,
  'useYn': 'Y',
  'applYmd': '20240401',
  'oldStoreCd': None,
  'newStoreCd': None,
  'fcType2': None,
  'hangCd1': None,
  'hangCd2': '11305',
  'hangCd3': None,
  'zipNo': '01010',
  'storeAddr1': None,
  'storeAddr2': None,
  'doroZipNo': '01010',
  'doroStoreAddr1': None,
  'doroStoreAddr2': None,
  'latVal': 37.649414,
  'longVal': 127.013301,
  'preStoreCd': None,
  'hour24Yn': 'Y',
  'friedYn': 'N',
  'bakeryYn': 'N',
  'coffeeYn': 'Y',
  'lottoYn': 'N',
  'totoYn': 'N',
  'atmYn': 'Y',
  'storeDscr': None,
  'deliveryYn': 'Y',
  'jumpoMultiDeviceYn': 'N',
  'jumpoPosCashYn': 'N',
  'jumpoBatteryYn': 'N',
  'jumpoDelivYn': 'N',
  'jumpoPickYn': 

In [225]:
cu_df = pd.DataFrame(cu_list)

In [243]:
cu_df

storeCd   storeNm  fcCd slcCd hangCd bumunCd teamCd  scCd   openYmd  \
0      45047   419사거리점  None  None     11    None   None  None  20230110   
1      49985     41타워점  None  None     11    None   None  None  20240726   
2      32354     63빌딩점  None  None     11    None   None  None  20180709   
3      39418    BGF사옥점  None  None     11    None   None  None  20210315   
4      44027  BNK금융타워점  None  None     11    None   None  None  20220831   
...      ...       ...   ...   ...    ...     ...    ...   ...       ...   
2954   02561    흑석명수대점  None  None     11    None   None  None  20000331   
2955   46717   흑석센트레빌점  None  None     11    None   None  None  20230731   
2956   17576     흑석현대점  None  None     11    None   None  None  20120419   
2957   49198   희윤이네편의점  None  None     11    None   None  None  20240429   
2958   01800     ＣＶＳ상품  None  None     11    None   None  None  20020215   

     closeYmd  ... plusSvcCommCd plusSvcUseYn storeplusYn exceptStoreCdList  \
0        None  ...          None         None           N              None   
1        None  ...          None         None           N              None   
2        None  ...          None         None           N              None   
3        None  ...          None         None           Y              None   
4        None  ...          None         None           N              None   
...       ...  ...           ...          ...         ...               ...   
2954     None  ...          None         None           N              None   
2955     None  ...          None         None           N              None   
2956     None  ...          None         None           N              None   
2957     None  ...          None         None           N              None   
2958     None  ...          None         None           N              None   

     directYn stockCdcYn alcProdYn alcCenterYn centerReserveYn onItemNo  
0        None       None      None        None            None     None  
1        None       None      None        None            None     None  
2        None       None      None        None            None     None  
3        None       None      None        None            None     None  
4        None       None      None        None            None     None  
...       ...        ...       ...         ...             ...      ...  
2954     None       None      None        None            None     None  
2955     None       None      None        None            None     None  
2956     None       None      None        None            None     None  
2957     None       None      None        None            None     None  
2958     None       None      None        None            None     None  

[2959 rows x 108 columns]

In [226]:
cu_df_seoul = cu_df[cu_df['addrFst'].str.find("서울특별시") > -1].copy()

In [228]:
cu_df_seoul['addrFst'].apply(lambda x : x.split()[0]).value_counts()

addrFst
서울특별시    2908
Name: count, dtype: int64

In [230]:
cu_df_seoul['gu'] = cu_df_seoul['addrFst'].apply(lambda x : x.split()[1])

In [231]:
cu_df_seoul

storeCd   storeNm  fcCd slcCd hangCd bumunCd teamCd  scCd   openYmd  \
0      45047   419사거리점  None  None     11    None   None  None  20230110   
1      49985     41타워점  None  None     11    None   None  None  20240726   
2      32354     63빌딩점  None  None     11    None   None  None  20180709   
3      39418    BGF사옥점  None  None     11    None   None  None  20210315   
4      44027  BNK금융타워점  None  None     11    None   None  None  20220831   
...      ...       ...   ...   ...    ...     ...    ...   ...       ...   
2954   02561    흑석명수대점  None  None     11    None   None  None  20000331   
2955   46717   흑석센트레빌점  None  None     11    None   None  None  20230731   
2956   17576     흑석현대점  None  None     11    None   None  None  20120419   
2957   49198   희윤이네편의점  None  None     11    None   None  None  20240429   
2958   01800     ＣＶＳ상품  None  None     11    None   None  None  20020215   

     closeYmd  ... plusSvcUseYn storeplusYn exceptStoreCdList directYn  \
0        None  ...         None           N              None     None   
1        None  ...         None           N              None     None   
2        None  ...         None           N              None     None   
3        None  ...         None           Y              None     None   
4        None  ...         None           N              None     None   
...       ...  ...          ...         ...               ...      ...   
2954     None  ...         None           N              None     None   
2955     None  ...         None           N              None     None   
2956     None  ...         None           N              None     None   
2957     None  ...         None           N              None     None   
2958     None  ...         None           N              None     None   

     stockCdcYn alcProdYn alcCenterYn centerReserveYn onItemNo    gu  
0          None      None        None            None     None   강북구  
1          None      None        None            None     None   양천구  
2          None      None        None            None     None  영등포구  
3          None      None        None            None     None   강남구  
4          None      None        None            None     None  영등포구  
...         ...       ...         ...             ...      ...   ...  
2954       None      None        None            None     None   동작구  
2955       None      None        None            None     None   동작구  
2956       None      None        None            None     None   동작구  
2957       None      None        None            None     None  영등포구  
2958       None      None        None            None     None   강남구  

[2908 rows x 109 columns]

In [236]:
cu_집계 = cu_df_seoul.groupby(['gu'])[['addrFst']].count()

In [238]:
cu_집계.sort_values(by = ['addrFst'], ascending=False)

addrFst
gu           
강남구       207
강서구       173
송파구       163
마포구       139
영등포구      139
관악구       137
서초구       136
동대문구      119
은평구       116
중구        113
강동구       112
광진구       112
구로구       109
서대문구      109
금천구       104
종로구       101
노원구       101
성동구       101
성북구       100
중랑구        98
동작구        92
양천구        89
강북구        88
용산구        76
도봉구        73
도붕구         1

In [241]:
gs_집계 = df.groupby(['gu'])[['address']].count()

In [242]:
pd.concat([gs_집계, cu_집계], axis=1)

address  addrFst
gu                    
강남구     274.0      207
강동구     119.0      112
강북구      79.0       88
강서구     187.0      173
관악구     157.0      137
광진구     104.0      112
구로구     127.0      109
금천구      97.0      104
노원구     129.0      101
도봉구      82.0       73
동대문구    116.0      119
동작구     117.0       92
마포구     192.0      139
서대문구     93.0      109
서초구     146.0      136
성동구      85.0      101
성북구     109.0      100
송파구     183.0      163
양천구      93.0       89
영등포구    177.0      139
용산구      84.0       76
은평구     133.0      116
종로구      76.0      101
중구      107.0      113
중랑구     117.0       98
도붕구       NaN        1